In [6]:
from dotenv import load_dotenv

load_dotenv()

True

In [1]:
import os
import re
import itertools
import json
import jsonlines
import pandas as pd
import pytz
from datasets import Dataset

from langchain.schema import Document
from langchain.retrievers import BM25Retriever, EnsembleRetriever
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough
from langchain_core.prompts import PromptTemplate
from langchain_openai import ChatOpenAI, OpenAIEmbeddings
from langchain_upstage import UpstageEmbeddings
from langchain_community.docstore.in_memory import InMemoryDocstore
from langchain_experimental.text_splitter import SemanticChunker
from langchain.retrievers.self_query.base import SelfQueryRetriever
from langchain.chains.query_constructor.base import AttributeInfo
from langchain_milvus.vectorstores import Milvus
from pymilvus import Collection
from uuid import uuid4

from datetime import datetime
from langchain.schema.runnable import RunnableLambda, RunnableParallel

from langchain_community.document_transformers import LongContextReorder
from langchain_core.runnables import RunnableLambda

from datetime import timedelta
from operator import itemgetter

from langchain_teddynote.retrievers import KiwiBM25Retriever

In [2]:
URI = 'http://127.0.0.1:19530/'

# embeddings = OpenAIEmbeddings(model='text-embedding-3-large')

embeddings=UpstageEmbeddings(
    model='solar-embedding-1-large-query'
)

vectorstore_table = Milvus(
  embedding_function=embeddings,
  connection_args={'uri':URI},
  index_params={'index_type': 'AUTOINDEX', 'metric_type': 'IP'},
  collection_name='table_v6'
)

In [4]:
def save_docs_to_jsonl(documents, file_path):
    with jsonlines.open(file_path, mode="w") as writer:
        for doc in documents:
            writer.write(doc.dict())

In [66]:
filepath = './chunked_jsonl/table_v6.jsonl'

splitted_doc = []
with open(filepath, 'r', encoding='utf-8') as file:
    for line in file:
        if line.startswith('\n('):
            continue
        data = json.loads(line)

        doc = Document(
            page_content=data['page_content'],
            metadata=data['metadata']
        )
        splitted_doc.append(doc)

In [67]:
import re

document = splitted_doc.copy()


In [16]:
document[40]

Document(metadata={'page': 34, 'source': './raw_pdf_copy3/KISWeekly제1090호(20240628).pdf', 'id': 487, 'issue_date': '5'}, page_content='### 표7. 내주 독일 경제 지표\n\n```html\n<table>\n  <tr>\n    <th>Date</th>\n    <th>Name</th>\n    <th>Survey</th>\n    <th>Actual</th>\n    <th>Prior</th>\n  </tr>\n  <tr>\n    <td>2024-06-28</td>\n    <td>수입물가지수 전월비</td>\n    <td>0.20%</td>\n    <td>-</td>\n    <td>0.70%</td>\n  </tr>\n  <tr>\n    <td>2024-06-28</td>\n    <td>수입물가지수 전년비</td>\n    <td>-0.30%</td>\n    <td>-</td>\n    <td>-1.70%</td>\n  </tr>\n  <tr>\n    <td>2024-06-28</td>\n    <td>실업자 변동 (단위:천)</td>\n    <td>15.0k</td>\n    <td>-</td>\n    <td>25.0k</td>\n  </tr>\n  <tr>\n    <td>2024-06-28</td>\n    <td>실업수당 청구율 SA</td>\n    <td>5.90%</td>\n    <td>-</td>\n    <td>5.90%</td>\n  </tr>\n  <tr>\n    <td>2024-07-01</td>\n    <td>HCOB 독일 제조업 PMI</td>\n    <td>43.4</td>\n    <td>-</td>\n    <td>43.4</td>\n  </tr>\n  <tr>\n    <td>2024-07-01</td>\n    <td>CPI (전년대비)</td>\n    <td>2.30%</td>\n    <

In [35]:
document

[Document(metadata={'page': 0, 'source': './raw_pdf_copy3/KISWeekly제1090호(20240628).pdf', 'id': 6, 'issue_date': '20240628'}, page_content='국내금리동향\n| 국내금리     | 6/28   | 전주대비   |\n|--------------|--------|------------|\n| 통안 2Y     | 3.245  | 0.015      |\n| 국고 3Y     | 3.177  | 0.027      |\n| 국고 10Y    | 3.260  | 0.035      |\n| KRW IRS 3Y  | 3.190  | 0.023      |\n| CD 91D      | 3.600  | 0.000      |\n| CP 91D      | 4.130  | -0.050     |\n| Call         | 3.640  | 0.080      |'),
 Document(metadata={'page': 0, 'source': './raw_pdf_copy3/KISWeekly제1090호(20240628).pdf', 'id': 8, 'issue_date': '20240628'}, page_content='해외금리동향\n| 해외금리   | 6/28   | 전주대비   |\n|------------|--------|------------|\n| 미국 2Y   | 0.047  | 0.006      |\n| 미국 5Y   | 0.043  | 0.067      |\n| 미국 10Y  | 0.043  | 0.077      |\n| 독일 2Y   | 0.028  | -0.001     |\n| 독일 10Y  | 0.025  | 0.053      |\n| 중국 2Y   | 0.016  | -0.077     |\n| 중국 10Y  | 0.022  | -0.047     |'),
 Document(metadata={'page': 2, 'source': './raw

In [29]:
test_result

{'2024-06-28', '2024-07-01', '2024-07-03', '2024-07-04'}

In [32]:
formatted_dates

'20240704'

In [49]:
d = []
for i in document:
    test = []
    if re.search(r'\d{4}-\d{2}-\d{2}', i.page_content):
        test.append(i)

    test_result = set()
    for i in test:
        for j in re.findall(r'\d{4}-\d{2}-\d{2}', i.page_content):
            if i.metadata['issue_date'] != j.replace('-', ''):
                test_result.add(j)

    for dates in test_result:
        formatted_dates = dates.replace('-','')
        
        new_doc = doc.copy()
        new_doc.metadata['issue_date'] = formatted_dates
        d.append(new_doc)

print(len(document))
print(len(d))

for doc in d:
    document.append(doc)

print(len(document))

2668
9246
11914


In [51]:
document

[Document(metadata={'page': 0, 'source': './raw_pdf_copy3/KISWeekly제1090호(20240628).pdf', 'id': 6, 'issue_date': '20240628'}, page_content='국내금리동향\n| 국내금리     | 6/28   | 전주대비   |\n|--------------|--------|------------|\n| 통안 2Y     | 3.245  | 0.015      |\n| 국고 3Y     | 3.177  | 0.027      |\n| 국고 10Y    | 3.260  | 0.035      |\n| KRW IRS 3Y  | 3.190  | 0.023      |\n| CD 91D      | 3.600  | 0.000      |\n| CP 91D      | 4.130  | -0.050     |\n| Call         | 3.640  | 0.080      |'),
 Document(metadata={'page': 0, 'source': './raw_pdf_copy3/KISWeekly제1090호(20240628).pdf', 'id': 8, 'issue_date': '20240628'}, page_content='해외금리동향\n| 해외금리   | 6/28   | 전주대비   |\n|------------|--------|------------|\n| 미국 2Y   | 0.047  | 0.006      |\n| 미국 5Y   | 0.043  | 0.067      |\n| 미국 10Y  | 0.043  | 0.077      |\n| 독일 2Y   | 0.028  | -0.001     |\n| 독일 10Y  | 0.025  | 0.053      |\n| 중국 2Y   | 0.016  | -0.077     |\n| 중국 10Y  | 0.022  | -0.047     |'),
 Document(metadata={'page': 2, 'source': './raw

In [52]:
save_docs_to_jsonl(document, './chunked_jsonl/table_v6_2.jsonl')

In [11]:
for i in document:
  if '2024-11-01' in i.page_content and '차이신' in i.page_content:
    print(i)

page_content='### 표9. 내주 중국 경제 지표

```html
<table>
  <tr>
    <th>Date</th>
    <th>Name</th>
    <th>Survey</th>
    <th>Actual</th>
    <th>Prior</th>
  </tr>
  <tr>
    <td>2024-11-01</td>
    <td>차이신 중국 PMI 제조업</td>
    <td>49.7</td>
    <td>50.3</td>
    <td>49.3</td>
  </tr>
  <tr>
    <td>2024-11-05</td>
    <td>차이신 중국 PMI 종합</td>
    <td>-</td>
    <td>-</td>
    <td>50.3</td>
  </tr>
  <tr>
    <td>2024-11-05</td>
    <td>차이신 중국 PMI 서비스업</td>
    <td>50.5</td>
    <td>-</td>
    <td>50.3</td>
  </tr>
  <tr>
    <td>2024-11-07</td>
    <td>수출 YoY</td>
    <td>4.30%</td>
    <td>-</td>
    <td>2.40%</td>
  </tr>
  <tr>
    <td>2024-11-07</td>
    <td>수입 YoY</td>
    <td>-2.80%</td>
    <td>-</td>
    <td>0.30%</td>
  </tr>
  <tr>
    <td>2024-11-07</td>
    <td>무역수지</td>
    <td>$73.35b</td>
    <td>-</td>
    <td>$81.71b</td>
  </tr>
  <tr>
    <td>2024-11-07</td>
    <td>수출 YoY CNY</td>
    <td>-</td>
    <td>-</td>
    <td>1.60%</td>
  </tr>
  <tr>
    <td>2024-11-07</td>
   

In [19]:
splitted_doc = document.copy()

In [9]:
save_docs_to_jsonl(document, './chunked_jsonl/table_v3_mdate_re_3.jsonl')

In [5]:
filepath = './chunked_jsonl/table_v3.jsonl'

splitted_doc = []
with open(filepath, 'r', encoding='utf-8') as file:
    for line in file:
        if line.startswith('\n('):
            continue
        data = json.loads(line)

        doc = Document(
            page_content=data['page_content'],
            metadata=data['metadata']
        )
        splitted_doc.append(doc)

In [11]:
len(document)

12254

In [17]:
len(splitted_doc)

2757

In [13]:
splitted_doc

[Document(metadata={'type': 'table', 'table': './raw_pdf_copy3/KISWeekly제1090호(20240628)\\6.png', 'page': 0, 'source': './raw_pdf_copy3/KISWeekly제1090호(20240628).pdf', 'id': 6, 'issue_date': '20240628'}, page_content='국내금리동향\n| 국내금리     | 6/28   | 전주대비   |\n|--------------|--------|------------|\n| 통안 2Y     | 3.245  | 0.015      |\n| 국고 3Y     | 3.177  | 0.027      |\n| 국고 10Y    | 3.260  | 0.035      |\n| KRW IRS 3Y  | 3.190  | 0.023      |\n| CD 91D      | 3.600  | 0.000      |\n| CP 91D      | 4.130  | -0.050     |\n| Call         | 3.640  | 0.080      |'),
 Document(metadata={'type': 'table', 'table': './raw_pdf_copy3/KISWeekly제1090호(20240628)\\8.png', 'page': 0, 'source': './raw_pdf_copy3/KISWeekly제1090호(20240628).pdf', 'id': 8, 'issue_date': '20240628'}, page_content='해외금리동향\n| 해외금리   | 6/28   | 전주대비   |\n|------------|--------|------------|\n| 미국 2Y   | 0.047  | 0.006      |\n| 미국 5Y   | 0.043  | 0.067      |\n| 미국 10Y  | 0.043  | 0.077      |\n| 독일 2Y   | 0.028  | -0.001     |

In [22]:
for i in splitted_doc[3000:]:
  if len(i.page_content) > 8191:
    print(i)
    print()

In [25]:
for i in splitted_doc:
  del i.metadata['type']
  del i.metadata['table']

In [57]:
import time
from uuid import uuid4
embeddings = OpenAIEmbeddings(model='text-embedding-3-large')

# embeddings=UpstageEmbeddings(
#     model='solar-embedding-1-large-query'
# )

vectorstore_table = Milvus(
  embedding_function=embeddings,
  connection_args={'uri':URI},
  index_params={'index_type': 'AUTOINDEX', 'metric_type': 'IP'},
  collection_name='table_v6'
)

# uuids = [str(uuid4()) for _ in range(len(splitted_doc))]

# vectorstore_table.add_documents(
#     documents=splitted_doc,
#     ids = uuids
# )

batch_size = 300
sleep_time = 0

for i in range(0, len(splitted_doc), batch_size):
    batch_docs = splitted_doc[i:i + batch_size]

    uuids = [str(uuid4()) for _ in range(len(batch_docs))]
    
    vectorstore_table.add_documents(documents=batch_docs, ids=uuids)
    
    if i + batch_size < len(splitted_doc):
        print(f"Batch {i//batch_size + 1} added, waiting for {sleep_time} seconds...")
        time.sleep(sleep_time)

Batch 1 added, waiting for 0 seconds...
Batch 2 added, waiting for 0 seconds...
Batch 3 added, waiting for 0 seconds...
Batch 4 added, waiting for 0 seconds...
Batch 5 added, waiting for 0 seconds...
Batch 6 added, waiting for 0 seconds...
Batch 7 added, waiting for 0 seconds...
Batch 8 added, waiting for 0 seconds...


In [58]:
llm = ChatOpenAI(model='gpt-4o-mini', temperature=0)

milvus_retriever = vectorstore_table.as_retriever(
    search_kwargs={'k':10}
)

bm25_retriver = KiwiBM25Retriever.from_documents(
    splitted_doc
)
bm25_retriver.k = 30

### 평가

In [59]:
def adjust_time_filter_to_week(time_filter):
    """
    특정 날짜(YYYY-MM-DD)가 주어진 경우, 해당 날짜를 포함하는 주(월~일)의
    첫 번째 날(월요일)과 마지막 날(일요일)로 변환하는 함수.

    :param time_filter: dict, {"start_date": datetime, "end_date": datetime}
    :return: dict, {"start_date": datetime, "end_date": datetime}
    """
    # Extract start_date and end_date from time_filter
    start_date = time_filter.start_date
    end_date = time_filter.end_date

    # Handle the case where start_date or end_date is None
    if start_date is None or end_date is None:
        if start_date is not None and end_date is None:
            start_of_week = start_date - timedelta(days=start_date.weekday())  # 월요일 찾기
            end_of_week = start_of_week + timedelta(days=6)  # 해당 주 일요일 찾기

            return {
                "start_date": start_of_week.replace(hour=0, minute=0, second=0),
                "end_date": end_of_week.replace(hour=23, minute=59, second=59)
            }
        elif end_date is not None and start_date is None:
            start_of_week = end_date - timedelta(days=end_date.weekday())  # 월요일 찾기
            end_of_week = start_of_week + timedelta(days=6)  # 해당 주 일요일 찾기

            return {
                "start_date": start_of_week.replace(hour=0, minute=0, second=0),
                "end_date": end_of_week.replace(hour=23, minute=59, second=59)
            }
        else:
            return None  # or return the time_filter as is if you prefer

    # 날짜가 동일한 경우, 주의 첫 번째 날(월요일)과 마지막 날(일요일)로 변경
    if start_date.year == end_date.year and start_date.month==end_date.month and start_date.day==end_date.day:
        start_of_week = start_date - timedelta(days=start_date.weekday())  # 월요일 찾기
        end_of_week = start_of_week + timedelta(days=6)  # 해당 주 일요일 찾기

        return {
            "start_date": start_of_week.replace(hour=0, minute=0, second=0),
            "end_date": end_of_week.replace(hour=23, minute=59, second=59)
        }

    # 날짜가 다르면 기존 time_filter 유지
    return {
        "start_date": start_date,
        "end_date": end_date
    }

In [60]:
from datetime import datetime
from typing import Optional
from pydantic import BaseModel
import instructor
from openai import OpenAI


class TimeFilter(BaseModel):
    start_date: Optional[datetime] = None
    end_date: Optional[datetime] = None

class SearchQuery(BaseModel):
    query: str
    time_filter: TimeFilter


client = instructor.from_openai(OpenAI())

issue_date = "2025-01-25"
responses = []

def convert_to_list(example):
    if isinstance(example["contexts"], list):
        contexts = example["contexts"]
    else:
        try:
            contexts = json.loads(example["contexts"])
        except json.JSONDecodeError as e:
            print(f"JSON Decode Error: {example['contexts']} - {e}")
            contexts = []
    return {"contexts": contexts}

prompt = PromptTemplate.from_template(
'''You are an assistant for question-answering tasks.
Use the following pieces of retrieved table to answer the question.
If you don't know the answer, just say that you don't know.
Answer simply.
Answer in Korean.

#Question:
{question}
#Context:
{context}

#Answer:'''
)

chain = (
    {'context' : itemgetter('context'), 'question': itemgetter('question')}
    | prompt
    | llm
    | StrOutputParser()
)


llm = ChatOpenAI(model='gpt-4o-mini', temperature=0)

df = pd.read_csv("./qa_ragas_250310.csv", index_col=False)
df = df[['question', 'ground_truth']]
df.ground_truth = df.apply(lambda x: x.ground_truth.split("'")[1].split("'")[0], axis=1)

test_dataset = Dataset.from_pandas(df)

result_ = []
batch_dataset = [question for question in test_dataset["question"]]
context = []
answer = []

for question in batch_dataset:
    response = client.chat.completions.create(
        model="gpt-4o",
        response_model=SearchQuery,
        messages=[
            {
                "role": "system",
                "content": f"""
                You are an AI assxistant that extracts date ranges from financial queries. 
                The current report date is {issue_date}. 
                Your task is to extract the relevant date or date range from the user's query 
                and format it in YYYY-MM-DD format.
                If no date is specified, answer with None value
                """,
            },
            {
                "role": "user",
                "content": question,
            },
        ],
    )

    parsed_dates = adjust_time_filter_to_week(response.time_filter)

    # parsed_dates를 순회하며 None인 경우도 처리
    if parsed_dates:
        start = parsed_dates['start_date']
        end=parsed_dates['end_date']
    else:
        start=None
        end = None

    if start is None or end is None:
        expr = None
    else:
        expr = f"issue_date > '{start.strftime('%Y%m%d')}' AND issue_date < '{end.strftime('%Y%m%d')}'"
        expr = expr


    invoked_milvus = milvus_retriever.invoke(question
                                      , expr=expr
                                    )
    invoked_bm25 = bm25_retriver.invoke(question)
    invoked_filtered = []
    for i in invoked_bm25:
        if expr != None:
            if i.metadata['issue_date'] >= expr.split("'")[1] and i.metadata['issue_date'] <= expr.split("'")[3]:
                invoked_filtered.append(i)
        else:
            invoked_filtered.append(i)
    
    invoked = invoked_milvus + invoked_filtered

    context.append(invoked)

    answer.append(chain.invoke({'question':question, 'context': invoked}))

if "contexts" in test_dataset.column_names:
    test_dataset = test_dataset.remove_columns(["contexts"]).add_column("contexts", [[j.page_content for j in i] for i in context])
else:
    test_dataset = test_dataset.add_column("contexts", [[j.page_content for j in i] for i in context])

if "answer" in test_dataset.column_names:
    test_dataset = test_dataset.remove_columns(["answer"]).add_column("answer", answer)
else:
    test_dataset = test_dataset.add_column("answer", answer)

test_dataset = test_dataset.map(convert_to_list)

from ragas import evaluate
from ragas.metrics import (
    context_recall,
    context_precision,
    AnswerCorrectness,
    answer_similarity
)

for _ in range(3):
    result = evaluate(
        dataset=test_dataset,
        metrics=[
            context_recall,
            context_precision,
            answer_similarity,
            AnswerCorrectness(weights=[0.75, 0.25]),
        ],
    )
    result_.append(result)

with open('./score/250313_table_date.json', "w", encoding='utf-8') as json_file:
    json.dump(result_, json_file, indent=4)

Map:   0%|          | 0/21 [00:00<?, ? examples/s]

c:\Users\Jo\AppData\Local\Programs\Python311\Lib\site-packages\ragas\metrics\__init__.py:1: LangChainDeprecationWarning: As of langchain-core 0.3.0, LangChain uses pydantic v2 internally. The langchain_core.pydantic_v1 module was a compatibility shim for pydantic v1, and should no longer be used. Please update the code to import from Pydantic directly.

For example, replace imports like: `from langchain_core.pydantic_v1 import BaseModel`
with: `from pydantic import BaseModel`
or the v1 compatibility namespace if you are working in a code base that has not been fully upgraded to pydantic 2 yet. 	from pydantic.v1 import BaseModel

  from ragas.metrics._answer_correctness import AnswerCorrectness, answer_correctness
c:\Users\Jo\AppData\Local\Programs\Python311\Lib\site-packages\ragas\metrics\__init__.py:4: LangChainDeprecationWarning: As of langchain-core 0.3.0, LangChain uses pydantic v2 internally. The langchain.pydantic_v1 module was a compatibility shim for pydantic v1, and should no 

Evaluating:   0%|          | 0/84 [00:00<?, ?it/s]

Exception raised in Job[56]: BadRequestError(Error code: 400 - {'error': {'message': "This model's maximum context length is 128000 tokens. However, your messages resulted in 133732 tokens. Please reduce the length of the messages.", 'type': 'invalid_request_error', 'param': 'messages', 'code': 'context_length_exceeded'}})


Evaluating:   0%|          | 0/84 [00:00<?, ?it/s]

Exception raised in Job[56]: BadRequestError(Error code: 400 - {'error': {'message': "This model's maximum context length is 128000 tokens. However, your messages resulted in 133732 tokens. Please reduce the length of the messages.", 'type': 'invalid_request_error', 'param': 'messages', 'code': 'context_length_exceeded'}})


Evaluating:   0%|          | 0/84 [00:00<?, ?it/s]

Exception raised in Job[56]: BadRequestError(Error code: 400 - {'error': {'message': "This model's maximum context length is 128000 tokens. However, your messages resulted in 133732 tokens. Please reduce the length of the messages.", 'type': 'invalid_request_error', 'param': 'messages', 'code': 'context_length_exceeded'}})


In [64]:
pd.set_option('display.max_rows', None)  # 모든 행 출력
pd.set_option('display.max_colwidth', None)  # 문자열 길이 제한 해제

In [ ]:
df[['question', 'ground_truth']]

question  \
0                          2024년 11월 15일 현재 통안 2년물 금리는 얼마입니까?   
1               2024년 11월 8일 FOMC 금리 결정에서 금리는 몇 퍼센트로 설정되었습니까?   
2                   2024년 10월 11일 기준으로 KRW IRS 1년물 금리는 얼마입니까?   
3   2024년 7월 26일 기준 10년 만기 채권 중 가장 높은 스프레드 차이를 보이는 등급은 무엇입니까?   
4        2025년 1월 첫째 주 전체 채권 중에서 가장 높은 비율을 차지하는 채권 유형은 무엇입니까?   
5                       24년 6월 말 단일기한부대금채권 중 가장 낮은 금리는 얼마입니까?   
6                         25년 1월 3일 기준 1년 만기 통안채의 수익률은 얼마입니까?   
7        25년 1월 둘째 주 ELS 전체 평균 상환 지급률은 지난 주와 이번 주에 각각 얼마였습니까?   
8              24년 12월 초 기준, 주택금융공사의 채권은 어떤 등급이며, 만기일은 언제입니까?   
9                    9월 둘째 주 기준 기아와 현대자동차의 신용등급은 어떻게 변경되었습니까?   
10                           25년 1월 10일 기준 KRW/USD 환율은 얼마입니까?   
11                    2024년 10월 14일에 발행된 부산은행의 은행채 금리는 얼마입니까?   
12                                     신한카드2240-1의 만기는 언제입니까?   
13           2024년 8월 2일 기준으로 KRW 1년물 CRS가 2.575에서 얼마로 변했습니까?   
14                             에스프로젝트이노 주식관련 투자액의 만기일은 언제입니까?   
15                                 이지스밸류리츠1-1(녹)의 발행일은 언제입니까?   
16               2024년 11월 1일에 발표된 차이신 중국 PMI 제조업 지수는 얼마였습니까?   
17                      2024년 8월 5일 차이신 중국 PMI 종합 지수는 얼마였습니까?   
18                              현대카드유니버스1차1-4 옵션의 만기일은 언제입니까?   
19                                  한국수출입금융(주)의 채권 등급은 무엇입니까?   
20        2024년 8월 19일에 발행된 은행채 중 가장 높은 금리를 가진 채권의 금리는 얼마입니까?   

                                              ground_truth  
0                                 현재 통안 2년물 금리는 2.975%입니다.  
1            2024년 11월 8일 FOMC 금리 결정에서 금리는 4.75%로 설정되었습니다.  
2             2024년 10월 11일 기준으로 KRW IRS 1년물 금리는 3.135입니다.  
3                 10년 만기 채권 중 가장 높은 수익률을 보이는 등급은 A- 등급입니다.  
4     2025년 1월 첫째 주 전체 채권 중에서 가장 높은 비율을 차지하는 채권 유형은 국채입니다.  
5                          단일기한부대금채권 중 가장 낮은 금리는 3.672입니다.  
6                               1년 만기 통안채의 수익률은 2.677%입니다.  
7                전체 평균 지급률은 지난 주에 5.86%였고, 이번 주에 6.6%였습니다.  
8               주택금융공사의 채권은 AAA 등급이며, 만기는 2025년 12월 2일입니다.  
9                    기아와 현대자동차는 AA+ 등급에서 AAA 등급으로 상향되었습니다.  
10                                    KRW/USD 환율은 1465입니다.  
11                 2024년 10월 14일에 발행된 부산은행의 금리는 3.220%입니다.  
12                       신한카드2240-1의 만기는 2027년 11월 11일입니다.  
13            2024년 8월 2일 기준으로 주간증감이 2.575에서 2.705로 변했습니다.  
14               에스프레소트리노의 주식관련 투자액의 만기일은 2025년 1월 15일입니다.  
15                   이지스밸류리츠1-1(녹)의 발행일은 2023년 11월 27일입니다.  
16              2024년 11월 1일 차이신 중국 PMI 제조업 지수는 50.3이었습니다.  
17                2024년 8월 5일 차이신 중국 PMI 종합 지수는 51.2이었습니다.  
18                 현대카드유니버스1차1-4 옵션의 만기일은 2025년 3월 15일입니다.  
19                              한국수출입금융(주)의 채권 등급은 AAA입니다.  
20  2024년 8월 19일에 발행된 채권 중 가장 높은 금리를 가진 채권의 금리는 3.350%입니다.

In [62]:
answer

['2024년 11월 15일 현재 통안 2년물 금리는 2.975%입니다.',
 '2024년 11월 8일 FOMC 금리 결정에서 금리는 4.75%로 설정되었습니다.',
 '2024년 10월 11일 기준으로 KRW IRS 1년물 금리는 3.135%입니다.',
 '2024년 7월 26일 기준 10년 만기 채권 중 가장 높은 스프레드 차이를 보이는 등급은 AA-입니다.',
 '2025년 1월 첫째 주 전체 채권 중에서 가장 높은 비율을 차지하는 채권 유형은 국채입니다.',
 '가장 낮은 금리는 3.326%입니다.',
 '25년 1월 3일 기준 1년 만기 통안채의 수익률은 2.62%입니다.',
 '25년 1월 둘째 주 ELS 전체 평균 상환 지급률은 지난 주 6.6%였고, 이번 주 4.84%입니다.',
 '주택금융공사의 채권 등급은 AAA이며, 만기일은 2024년 12월 10일입니다.',
 '기아와 현대자동차의 신용등급 변동에 대한 정보는 제공되지 않았습니다. 따라서 답변을 드릴 수 없습니다.',
 '2025년 1월 10일 기준 KRW/USD 환율은 1465입니다.',
 '부산은행의 2024년 10월 14일에 발행된 은행채 금리는 3.35%입니다.',
 '신한카드2240-1의 만기는 2027년 11월 11일입니다.',
 '2024년 8월 2일 기준으로 KRW 1년물 CRS는 2.575로, 이전의 2.705에서 0.13 감소했습니다.',
 '에스프로젝트이노 주식관련 투자액의 만기일은 2025년 4월 15일입니다.',
 '이지스밸류리츠1-1(녹)의 발행일은 2023-11-27입니다.',
 '2024년 11월 1일에 발표된 차이신 중국 PMI 제조업 지수는 50.3이었습니다.',
 '2024년 8월 5일 차이신 중국 PMI 종합 지수는 51.2였습니다.',
 '현대카드유니버스1차1-4 옵션의 만기일은 2025년 3월 15일입니다.',
 '한국수출입금융(주)의 채권 등급은 AAA입니다.',
 '2024년 8월 19일에 발행된 은행채 중 가장 높은 금리를 가진 채권의 금리는 3

In [65]:
df['ground_truth']

0                                   현재 통안 2년물 금리는 2.975%입니다.
1              2024년 11월 8일 FOMC 금리 결정에서 금리는 4.75%로 설정되었습니다.
2               2024년 10월 11일 기준으로 KRW IRS 1년물 금리는 3.135입니다.
3                   10년 만기 채권 중 가장 높은 수익률을 보이는 등급은 A- 등급입니다.
4       2025년 1월 첫째 주 전체 채권 중에서 가장 높은 비율을 차지하는 채권 유형은 국채입니다.
5                            단일기한부대금채권 중 가장 낮은 금리는 3.672입니다.
6                                 1년 만기 통안채의 수익률은 2.677%입니다.
7                  전체 평균 지급률은 지난 주에 5.86%였고, 이번 주에 6.6%였습니다.
8                 주택금융공사의 채권은 AAA 등급이며, 만기는 2025년 12월 2일입니다.
9                      기아와 현대자동차는 AA+ 등급에서 AAA 등급으로 상향되었습니다.
10                                      KRW/USD 환율은 1465입니다.
11                   2024년 10월 14일에 발행된 부산은행의 금리는 3.220%입니다.
12                         신한카드2240-1의 만기는 2027년 11월 11일입니다.
13              2024년 8월 2일 기준으로 주간증감이 2.575에서 2.705로 변했습니다.
14                 에스프레소트리노의 주식관련 투자액의 만기일은 2025년 1월 15일입니다.
15                     이지스밸류리츠1-1(녹)의 발행일은 2023년 11월 27일입니다.
16                2024년 

In [ ]:
df['ground_truth'][20]

'2024년 8월 19일에 발행된 채권 중 가장 높은 금리를 가진 채권의 금리는 3.350%입니다.'

In [ ]:
context[2]

[Document(metadata={'pk': 'd9cbcee1-f0ce-4f2f-864f-bbe6136d4f02', 'page': 41, 'source': 'parsed_pdf\\KISWeekly제1105호(20241011).pdf', 'issue_date': '20241011'}, page_content='KRW IRS (단위: %)\n\n|차이|10/11/2024|10/4/2024|\n|---|---|---|\n|4.00%| |0.200%|\n|3.50%| |0.150%|\n|3.00%| |0.100%|\n|2.50%| |0.050%|\n|2.00%| | |\n|1.50%| |0.000%|\n|1.00%| |-0.050%|\n|0.50%| |-0.100%|\n|0.00%| |-0.150%|\n\n자료 : Refinitiv, Bloomberg'),
 Document(metadata={'pk': '68a17663-62a1-479e-b18a-c25b20f53251', 'page': 42, 'source': 'parsed_pdf\\KISWeekly제1105호(20241011).pdf', 'issue_date': '20241011'}, page_content='KRW CRS\n\n|차이|10/11/2024|10/4/2024|\n|---|---|---|\n|3.00%| |0.20%|\n| | |0.18%|\n|2.50%| |0.16%|\n|2.00%| |0.14%|\n| | |0.12%|\n|1.50%| |0.10%|\n|1.00%| |0.08%|\n| | |0.06%|\n|0.50%| |0.04%|\n| | |0.02%|\n|0.00%| |0.00%|\n\n자료 : Refinitiv, Bloomberg'),
 Document(metadata={'pk': '5b61f8aa-4b87-4bb6-b79f-58724e4e1275', 'page': 41, 'source': 'parsed_pdf\\KISWeekly제1105호(20241011).pdf', 'issue_date'

In [53]:
print(context[9][0].page_content)

3사 신용등급 변경 현황
| 회사명          | 변경일      | 종류 | 등급변경내역 | 이전  | 이후  | 한신평 | 등급 | 평가일      | NICE | 등급 | 평가일      | 한기평 | 등급 | 평가일      |
|------------------|-------------|------|--------------|-------|-------|--------|------|-------------|------|------|-------------|--------|------|-------------|
| 기아             | 2024-09-10  | BOND | AA+          | AAA   | AAA   | 2024-09-10 | AAA  | 2024-09-10  |      |      |             |        |      |             |
| 현대자동차       | 2024-09-10  | BOND | AA+          | AAA   | AAA   | 2024-09-10 | AAA  | 2024-09-10  |      |      |             |        |      |             |
| 현대카드         | 2024-09-11  | BOND | AA0          | AA+   | AA+   | 2024-09-11 | AA+  | 2024-09-11  |      |      |             |        |      |             |
| 멜로우제1차(유)1 | 2024-09-11  | ABS  | A+           | AA-   | AA-   | 2024-09-11 | AA-  | 2024-09-11  |      |      |             |        |      |             |


In [66]:
import gc
gc.collect()

19259

In [61]:
import time
from uuid import uuid4
embeddings = OpenAIEmbeddings(model='text-embedding-3-large')

# embeddings=UpstageEmbeddings(
#     model='solar-embedding-1-large-query'
# )
splitted_doc = document.copy()
vectorstore_table = Milvus(
  embedding_function=embeddings,
  connection_args={'uri':URI},
  index_params={'index_type': 'AUTOINDEX', 'metric_type': 'IP'},
  collection_name='table_v6_2'
)

# uuids = [str(uuid4()) for _ in range(len(splitted_doc))]

# vectorstore_table.add_documents(
#     documents=splitted_doc,
#     ids = uuids
# )

batch_size = 300
sleep_time = 0

for i in range(0, len(splitted_doc), batch_size):
    batch_docs = splitted_doc[i:i + batch_size]

    uuids = [str(uuid4()) for _ in range(len(batch_docs))]
    
    vectorstore_table.add_documents(documents=batch_docs, ids=uuids)
    
    if i + batch_size < len(splitted_doc):
        print(f"Batch {i//batch_size + 1} added, waiting for {sleep_time} seconds...")
        time.sleep(sleep_time)

KeyboardInterrupt: 

In [ ]:
llm = ChatOpenAI(model='gpt-4o-mini', temperature=0)

milvus_retriever = vectorstore_table.as_retriever(
    search_kwargs={'k':10}
)

bm25_retriver = KiwiBM25Retriever.from_documents(
    splitted_doc
)
bm25_retriver.k = 30

In [ ]:
from datetime import datetime
from typing import Optional
from pydantic import BaseModel
import instructor
from openai import OpenAI


class TimeFilter(BaseModel):
    start_date: Optional[datetime] = None
    end_date: Optional[datetime] = None

class SearchQuery(BaseModel):
    query: str
    time_filter: TimeFilter


client = instructor.from_openai(OpenAI())

issue_date = "2025-01-25"
responses = []

def convert_to_list(example):
    if isinstance(example["contexts"], list):
        contexts = example["contexts"]
    else:
        try:
            contexts = json.loads(example["contexts"])
        except json.JSONDecodeError as e:
            print(f"JSON Decode Error: {example['contexts']} - {e}")
            contexts = []
    return {"contexts": contexts}

prompt = PromptTemplate.from_template(
'''You are an assistant for question-answering tasks.
Use the following pieces of retrieved table to answer the question.
If you don't know the answer, just say that you don't know.
Answer simply.
Answer in Korean.

#Question:
{question}
#Context:
{context}

#Answer:'''
)

chain = (
    {'context' : itemgetter('context'), 'question': itemgetter('question')}
    | prompt
    | llm
    | StrOutputParser()
)


llm = ChatOpenAI(model='gpt-4o-mini', temperature=0)

df = pd.read_csv("./qa_ragas_250310.csv", index_col=False)
df = df[['question', 'ground_truth']]
df.ground_truth = df.apply(lambda x: x.ground_truth.split("'")[1].split("'")[0], axis=1)

test_dataset = Dataset.from_pandas(df)

result_ = []
batch_dataset = [question for question in test_dataset["question"]]
context = []
answer = []

for question in batch_dataset:
    response = client.chat.completions.create(
        model="gpt-4o",
        response_model=SearchQuery,
        messages=[
            {
                "role": "system",
                "content": f"""
                You are an AI assxistant that extracts date ranges from financial queries. 
                The current report date is {issue_date}. 
                Your task is to extract the relevant date or date range from the user's query 
                and format it in YYYY-MM-DD format.
                If no date is specified, answer with None value
                """,
            },
            {
                "role": "user",
                "content": question,
            },
        ],
    )

    parsed_dates = adjust_time_filter_to_week(response.time_filter)

    # parsed_dates를 순회하며 None인 경우도 처리
    if parsed_dates:
        start = parsed_dates['start_date']
        end=parsed_dates['end_date']
    else:
        start=None
        end = None

    if start is None or end is None:
        expr = None
    else:
        expr = f"issue_date > '{start.strftime('%Y%m%d')}' AND issue_date < '{end.strftime('%Y%m%d')}'"
        expr = expr


    invoked_milvus = milvus_retriever.invoke(question
                                      , expr=expr
                                    )
    invoked_bm25 = bm25_retriver.invoke(question)
    invoked_filtered = []
    for i in invoked_bm25:
        if expr != None:
            if i.metadata['issue_date'] >= expr.split("'")[1] and i.metadata['issue_date'] <= expr.split("'")[3]:
                invoked_filtered.append(i)
        else:
            invoked_filtered.append(i)
    
    invoked = invoked_milvus + invoked_filtered

    context.append(invoked)

    answer.append(chain.invoke({'question':question, 'context': invoked}))

if "contexts" in test_dataset.column_names:
    test_dataset = test_dataset.remove_columns(["contexts"]).add_column("contexts", [[j.page_content for j in i] for i in context])
else:
    test_dataset = test_dataset.add_column("contexts", [[j.page_content for j in i] for i in context])

if "answer" in test_dataset.column_names:
    test_dataset = test_dataset.remove_columns(["answer"]).add_column("answer", answer)
else:
    test_dataset = test_dataset.add_column("answer", answer)

test_dataset = test_dataset.map(convert_to_list)

from ragas import evaluate
from ragas.metrics import (
    context_recall,
    context_precision,
    AnswerCorrectness,
    answer_similarity
)

for _ in range(3):
    result = evaluate(
        dataset=test_dataset,
        metrics=[
            context_recall,
            context_precision,
            answer_similarity,
            AnswerCorrectness(weights=[0.75, 0.25]),
        ],
    )
    result_.append(result)

with open('./score/250313_table_date_2.json', "w", encoding='utf-8') as json_file:
    json.dump(result_, json_file, indent=4)